In [1]:
import requests
from bs4 import BeautifulSoup
import re
import pandas as pd
from requests_html import HTMLSession, AsyncHTMLSession
import asyncio
import time
import os

MAX_CONCURRENT_CHROME = 4  # Set the maximum number of concurrent Chrome instances
semaphore = asyncio.Semaphore(MAX_CONCURRENT_CHROME)

In [2]:
pattern = re.compile(r'^ResponsiveImageContainer.*')
block_pattern = re.compile(r'^(?!Vogue Runway$)(?!Profile).*$')
prefix = re.compile(r'https://www.vogue.com/fashion-shows/|slideshow/')
parent_folder_name = "../secrets/pics/"

In [3]:
async def download(url, n_pics, folder_name, max_retries=5):
    async with semaphore:
        all_name = re.sub(prefix, '', url)
        all_name = name = re.sub('/', '_', all_name)
        
        for i in range(1, n_pics+1):
            retries = 0
            slide_url = url + f"#{i}"
            
            while retries < max_retries:
                try:
                    session = AsyncHTMLSession()
                    # Send a GET request to the URL
                    response = await session.get(slide_url)
                    
                    # Render the JavaScript on the page (if needed)
                    await response.html.arender()
                    
                    # Use BeautifulSoup to parse the HTML
                    soup = BeautifulSoup(response.html.html, 'html.parser')
                    
                    # Extract desired data; for example, all headings
                    images = soup.find_all('img', {'class': pattern, 'alt': block_pattern})
                    
                    if images:
                        img_url = images[0]['src']

                        img_data = requests.get(img_url).content

                        name = folder_name + all_name + f"#{i}.jpg"
                        
                        if img_data:
                            with open(name, 'wb') as file:
                                file.write(img_data)
                        
                        await session.close()
                        break
                    else:
                        retries += 1
                        print("Retry", url, "retries:", retries)
                        time.sleep(0.5)
                
                except Exception as e:
                    print(f"Error loading {url}")
                    retries += 1
                    time.sleep(0.5)
                finally:
                    await session.close()
                
            # await session.close()
            # del session


async def run_tasks(s, folder):
    tasks = []
    for idx, row in s.iterrows():
        task = download(row['show_url'], row['n_pics'], folder)
        tasks.append(task)
    results = await asyncio.gather(*tasks)
    return results

In [4]:
df_long = pd.read_csv('../secrets/shows_season_long.csv').dropna()
df_long['n_pics'] = df_long['n_pics'].astype(int)
df_long

showID  year                                         season_url  \
0          0  2006  https://www.vogue.com/fashion-shows/fall-2006-...   
1          1  2006  https://www.vogue.com/fashion-shows/fall-2006-...   
2          2  2006  https://www.vogue.com/fashion-shows/fall-2006-...   
3          3  2006  https://www.vogue.com/fashion-shows/fall-2006-...   
4          4  2006  https://www.vogue.com/fashion-shows/fall-2006-...   
...      ...   ...                                                ...   
4217    4217  2012  https://www.vogue.com/fashion-shows/fall-2012-...   
4218    4218  2012  https://www.vogue.com/fashion-shows/fall-2012-...   
4219    4219  2012  https://www.vogue.com/fashion-shows/fall-2012-...   
4220    4220  2012  https://www.vogue.com/fashion-shows/fall-2012-...   
4221    4221  2012  https://www.vogue.com/fashion-shows/fall-2012-...   

                                               show_url  n_pics  
0     https://www.vogue.com/fashion-shows/fall-2006-...      40  
1     https://www.vogue.com/fashion-shows/fall-2006-...      48  
2     https://www.vogue.com/fashion-shows/fall-2006-...      69  
3     https://www.vogue.com/fashion-shows/fall-2006-...      26  
4     https://www.vogue.com/fashion-shows/fall-2006-...      38  
...                                                 ...     ...  
4217  https://www.vogue.com/fashion-shows/fall-2012-...      22  
4218  https://www.vogue.com/fashion-shows/fall-2012-...      25  
4219  https://www.vogue.com/fashion-shows/fall-2012-...      12  
4220  https://www.vogue.com/fashion-shows/fall-2012-...      23  
4221  https://www.vogue.com/fashion-shows/fall-2012-...      31  

[4204 rows x 5 columns]

In [5]:
epoch = 1
GAP = 100
start = epoch * GAP
end = start + GAP

directory = parent_folder_name + f"shows_{start}_{end}/"

if not os.path.exists(directory):
    os.makedirs(directory)
    print(f"Directory '{directory}' created.")
else:
    print(f"Directory '{directory}' already exists.")
await run_tasks(df_long[['show_url', 'n_pics']][start:end], directory)

Directory 'data/pics/shows_0_100/' created.


Future exception was never retrieved
future: <Future finished exception=NetworkError('Protocol error (Target.sendMessageToTarget): No session with given id')>
pyppeteer.errors.NetworkError: Protocol error (Target.sendMessageToTarget): No session with given id
Future exception was never retrieved
future: <Future finished exception=NetworkError('Protocol error (Target.sendMessageToTarget): No session with given id')>
pyppeteer.errors.NetworkError: Protocol error (Target.sendMessageToTarget): No session with given id
Future exception was never retrieved
future: <Future finished exception=NetworkError('Protocol error (Target.sendMessageToTarget): No session with given id')>
pyppeteer.errors.NetworkError: Protocol error (Target.sendMessageToTarget): No session with given id
Future exception was never retrieved
future: <Future finished exception=NetworkError('Protocol error (Target.sendMessageToTarget): No session with given id')>
pyppeteer.errors.NetworkError: Protocol error (Target.sendMes

Error loading https://www.vogue.com/fashion-shows/fall-2006-ready-to-wear/burberry-prorsum/slideshow/collection


Future exception was never retrieved
future: <Future finished exception=NetworkError('Protocol error (Target.sendMessageToTarget): No session with given id')>
pyppeteer.errors.NetworkError: Protocol error (Target.sendMessageToTarget): No session with given id
Future exception was never retrieved
future: <Future finished exception=NetworkError('Protocol error (Target.sendMessageToTarget): No session with given id')>
pyppeteer.errors.NetworkError: Protocol error (Target.sendMessageToTarget): No session with given id
Future exception was never retrieved
future: <Future finished exception=NetworkError('Protocol error (Target.sendMessageToTarget): No session with given id')>
pyppeteer.errors.NetworkError: Protocol error (Target.sendMessageToTarget): No session with given id
Future exception was never retrieved
future: <Future finished exception=NetworkError('Protocol error (Target.sendMessageToTarget): No session with given id')>
pyppeteer.errors.NetworkError: Protocol error (Target.sendMes

Error loading https://www.vogue.com/fashion-shows/fall-2006-ready-to-wear/gucci/slideshow/collection


...

Future exception was never retrieved
future: <Future finished exception=NetworkError('Protocol error (Target.sendMessageToTarget): No session with given id')>
pyppeteer.errors.NetworkError: Protocol error (Target.sendMessageToTarget): No session with given id
Future exception was never retrieved
future: <Future finished exception=NetworkError('Protocol error (Target.sendMessageToTarget): No session with given id')>
pyppeteer.errors.NetworkError: Protocol error (Target.sendMessageToTarget): No session with given id


Retry https://www.vogue.com/fashion-shows/resort-2020/balenciaga/slideshow/collection retries: 1
Retry https://www.vogue.com/fashion-shows/resort-2020/balenciaga/slideshow/collection retries: 2
Retry https://www.vogue.com/fashion-shows/resort-2020/balenciaga/slideshow/collection retries: 3
Retry https://www.vogue.com/fashion-shows/resort-2020/balenciaga/slideshow/collection retries: 4
Retry https://www.vogue.com/fashion-shows/resort-2020/balenciaga/slideshow/collection retries: 5


Future exception was never retrieved
future: <Future finished exception=NetworkError('Protocol error (Target.sendMessageToTarget): No session with given id')>
pyppeteer.errors.NetworkError: Protocol error (Target.sendMessageToTarget): No session with given id


Retry https://www.vogue.com/fashion-shows/resort-2020/balenciaga/slideshow/collection retries: 1
Retry https://www.vogue.com/fashion-shows/resort-2020/dior-homme/slideshow/collection retries: 1
Retry https://www.vogue.com/fashion-shows/resort-2020/dior-homme/slideshow/collection retries: 2
Retry https://www.vogue.com/fashion-shows/resort-2020/dior-homme/slideshow/collection retries: 3
Retry https://www.vogue.com/fashion-shows/resort-2020/dior-homme/slideshow/collection retries: 4
Retry https://www.vogue.com/fashion-shows/resort-2020/dior-homme/slideshow/collection retries: 5
Retry https://www.vogue.com/fashion-shows/resort-2020/dior-homme/slideshow/collection retries: 1
Retry https://www.vogue.com/fashion-shows/resort-2020/dior-homme/slideshow/collection retries: 2
Retry https://www.vogue.com/fashion-shows/resort-2020/dior-homme/slideshow/collection retries: 3


[None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None]

In [5]:
df_per_year = df_long.groupby(df_long['year']).first()

In [6]:
directory = "../secrets/pics/shows_1peryear/"

await run_tasks(df_per_year[['show_url', 'n_pics']], directory)

Future exception was never retrieved
future: <Future finished exception=NetworkError('Protocol error Target.detachFromTarget: Target closed.')>
pyppeteer.errors.NetworkError: Protocol error Target.detachFromTarget: Target closed.
Future exception was never retrieved
future: <Future finished exception=NetworkError('Protocol error (Target.sendMessageToTarget): No session with given id')>
pyppeteer.errors.NetworkError: Protocol error (Target.sendMessageToTarget): No session with given id
Future exception was never retrieved
future: <Future finished exception=NetworkError('Protocol error Target.sendMessageToTarget: Target closed.')>
pyppeteer.errors.NetworkError: Protocol error Target.sendMessageToTarget: Target closed.
Future exception was never retrieved
future: <Future finished exception=NetworkError('Protocol error (Target.sendMessageToTarget): No session with given id')>
pyppeteer.errors.NetworkError: Protocol error (Target.sendMessageToTarget): No session with given id
Future excepti

Retry https://www.vogue.com/fashion-shows/spring-1990-ready-to-wear/azzedine-alaia/slideshow/collection retries: 1
Retry https://www.vogue.com/fashion-shows/spring-1990-ready-to-wear/azzedine-alaia/slideshow/collection retries: 2
Retry https://www.vogue.com/fashion-shows/spring-1990-ready-to-wear/azzedine-alaia/slideshow/collection retries: 3
Retry https://www.vogue.com/fashion-shows/spring-1990-ready-to-wear/azzedine-alaia/slideshow/collection retries: 4


Future exception was never retrieved
future: <Future finished exception=NetworkError('Protocol error (Target.sendMessageToTarget): No session with given id')>
pyppeteer.errors.NetworkError: Protocol error (Target.sendMessageToTarget): No session with given id
Future exception was never retrieved
future: <Future finished exception=NetworkError('Protocol error Target.detachFromTarget: Target closed.')>
pyppeteer.errors.NetworkError: Protocol error Target.detachFromTarget: Target closed.
Future exception was never retrieved
future: <Future finished exception=NetworkError('Protocol error (Target.sendMessageToTarget): No session with given id')>
pyppeteer.errors.NetworkError: Protocol error (Target.sendMessageToTarget): No session with given id
Future exception was never retrieved
future: <Future finished exception=NetworkError('Protocol error Target.sendMessageToTarget: Target closed.')>
pyppeteer.errors.NetworkError: Protocol error Target.sendMessageToTarget: Target closed.
Future excepti

Error loading https://www.vogue.com/fashion-shows/fall-1989-ready-to-wear/azzedine-alaia/slideshow/collection


Future exception was never retrieved
future: <Future finished exception=NetworkError('Protocol error Target.sendMessageToTarget: Target closed.')>
pyppeteer.errors.NetworkError: Protocol error Target.sendMessageToTarget: Target closed.
Future exception was never retrieved
future: <Future finished exception=NetworkError('Protocol error (Target.sendMessageToTarget): No session with given id')>
pyppeteer.errors.NetworkError: Protocol error (Target.sendMessageToTarget): No session with given id
Future exception was never retrieved
future: <Future finished exception=NetworkError('Protocol error (Target.sendMessageToTarget): No session with given id')>
pyppeteer.errors.NetworkError: Protocol error (Target.sendMessageToTarget): No session with given id
Future exception was never retrieved
future: <Future finished exception=NetworkError('Protocol error (Target.sendMessageToTarget): No session with given id')>
pyppeteer.errors.NetworkError: Protocol error (Target.sendMessageToTarget): No sessio

...

Error loading https://www.vogue.com/fashion-shows/fall-2024-menswear/nhoolywood-test-product-exchange-service/slideshow/collection


Future exception was never retrieved
future: <Future finished exception=NetworkError('Protocol error (Target.sendMessageToTarget): No session with given id')>
pyppeteer.errors.NetworkError: Protocol error (Target.sendMessageToTarget): No session with given id
Future exception was never retrieved
future: <Future finished exception=NetworkError('Protocol error (Target.sendMessageToTarget): No session with given id')>
pyppeteer.errors.NetworkError: Protocol error (Target.sendMessageToTarget): No session with given id
Future exception was never retrieved
future: <Future finished exception=NetworkError('Protocol error (Target.sendMessageToTarget): No session with given id')>
pyppeteer.errors.NetworkError: Protocol error (Target.sendMessageToTarget): No session with given id
Future exception was never retrieved
future: <Future finished exception=NetworkError('Protocol error (Target.sendMessageToTarget): No session with given id')>
pyppeteer.errors.NetworkError: Protocol error (Target.sendMes

Error loading https://www.vogue.com/fashion-shows/resort-2021-menswear/salvatore-ferragamo/slideshow/collection
Retry https://www.vogue.com/fashion-shows/fall-2024-menswear/nhoolywood-test-product-exchange-service/slideshow/collection retries: 2
Retry https://www.vogue.com/fashion-shows/fall-2024-menswear/nhoolywood-test-product-exchange-service/slideshow/collection retries: 3


Future exception was never retrieved
future: <Future finished exception=NetworkError('Protocol error (Target.sendMessageToTarget): No session with given id')>
pyppeteer.errors.NetworkError: Protocol error (Target.sendMessageToTarget): No session with given id
Future exception was never retrieved
future: <Future finished exception=NetworkError('Protocol error (Target.sendMessageToTarget): No session with given id')>
pyppeteer.errors.NetworkError: Protocol error (Target.sendMessageToTarget): No session with given id
Future exception was never retrieved
future: <Future finished exception=NetworkError('Protocol error (Target.sendMessageToTarget): No session with given id')>
pyppeteer.errors.NetworkError: Protocol error (Target.sendMessageToTarget): No session with given id
Future exception was never retrieved
future: <Future finished exception=NetworkError('Protocol error (Target.sendMessageToTarget): No session with given id')>
pyppeteer.errors.NetworkError: Protocol error (Target.sendMes

[None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None]